In [1]:
import cv2
import mediapipe as mp
import numpy as np

# Init MediaPipe
mp_pose = mp.solutions.pose
mp_selfie_segmentation = mp.solutions.selfie_segmentation
pose = mp_pose.Pose(static_image_mode=True)
segmentor = mp_selfie_segmentation.SelfieSegmentation(model_selection=1)

# Load image
image = cv2.imread("/home/siamai/data/Penguin/week7/Screenshot 2025-06-15 194901.png")
rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)

# Get segmentation mask
seg_result = segmentor.process(rgb)
mask = seg_result.segmentation_mask
condition = mask > 0.5

# Make background transparent (optional)
bg_image = np.zeros(image.shape, dtype=np.uint8)
segmented_image = np.where(condition[..., None], image, bg_image)

# Get skeleton
pose_result = pose.process(rgb)

if pose_result.pose_landmarks:
    for lm in pose_result.pose_landmarks.landmark:
        x, y = int(lm.x * image.shape[1]), int(lm.y * image.shape[0])
        cv2.circle(segmented_image, (x, y), 3, (0, 255, 0), -1)

# Show result
cv2.imshow("Segmented + Skeleton", segmented_image)
cv2.waitKey(0)
cv2.destroyAllWindows()

: 

In [1]:
import cv2
import mediapipe as mp
import numpy as np
import os

# === Init MediaPipe ===
mp_pose = mp.solutions.pose
mp_segmentation = mp.solutions.selfie_segmentation
pose = mp_pose.Pose()
segmentor = mp_segmentation.SelfieSegmentation(model_selection=1)

# === Input/Output Video ===
input_path = "/home/siamai/data/week7/train/train/Gary Oldman/Gary Oldman Interview 2 (Descending).mp4"
output_path = "cropped_person_output.mp4"
cap = cv2.VideoCapture(input_path)

width  = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))
fps    = cap.get(cv2.CAP_PROP_FPS)

fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter(output_path, fourcc, fps, (width, height))

frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
print(f"Total frames: {frame_count}")

# === Process Frame-by-Frame ===
while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
    
    # Get segmentation mask
    seg = segmentor.process(rgb)
    mask = seg.segmentation_mask
    condition = mask > 0.5

    # Get pose landmarks (to crop more tightly)
    res = pose.process(rgb)

    # Apply segmentation to mask background
    bg = np.zeros(frame.shape, dtype=np.uint8)
    segmented = np.where(condition[..., None], frame, bg)

    # Optional: crop around keypoints (tight bounding box)
    if res.pose_landmarks:
        h, w, _ = frame.shape
        xs = [lm.x * w for lm in res.pose_landmarks.landmark]
        ys = [lm.y * h for lm in res.pose_landmarks.landmark]
        x_min, x_max = int(max(min(xs) - 20, 0)), int(min(max(xs) + 20, w))
        y_min, y_max = int(max(min(ys) - 20, 0)), int(min(max(ys) + 20, h))
        cropped = segmented[y_min:y_max, x_min:x_max]
        # Resize back to original size
        cropped_resized = cv2.resize(cropped, (width, height))
        out.write(cropped_resized)
    else:
        out.write(segmented)  # fallback

cap.release()
out.release()
cv2.destroyAllWindows()
print(f"✅ Saved to {output_path}")


I0000 00:00:1750086559.941262 1167030 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1750086559.987276 1167071 gl_context.cc:357] GL version: 3.2 (OpenGL ES 3.2 NVIDIA 575.57.08), renderer: NVIDIA H100 80GB HBM3/PCIe/SSE2
I0000 00:00:1750086559.990204 1167030 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
INFO: Created TensorFlow Lite XNNPACK delegate for CPU.
I0000 00:00:1750086560.016548 1167084 gl_context.cc:357] GL version: 3.2 (OpenGL ES 3.2 NVIDIA 575.57.08), renderer: NVIDIA H100 80GB HBM3/PCIe/SSE2


Total frames: 3575
✅ Saved to cropped_person_output.mp4


In [2]:
import cv2
import mediapipe as mp
import numpy as np
import os

# === Init MediaPipe ===
mp_pose = mp.solutions.pose
mp_segmentation = mp.solutions.selfie_segmentation
pose = mp_pose.Pose(static_image_mode=False, model_complexity=1, enable_segmentation=True)
segmentor = mp_segmentation.SelfieSegmentation(model_selection=1)

# === Input/Output ===
input_path = "/home/siamai/data/week7/train/train/Gary Oldman/Gary Oldman Interview 2 (Descending).mp4"
output_folder = "cropped_frames"
os.makedirs(output_folder, exist_ok=True)

cap = cv2.VideoCapture(input_path)
frame_idx = 0

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
    
    # Get segmentation mask
    seg_result = segmentor.process(rgb)
    seg_mask = seg_result.segmentation_mask > 0.5
    seg_image = np.where(seg_mask[..., None], frame, 0)

    # Pose detection
    pose_result = pose.process(rgb)

    # No pose found
    if not pose_result.pose_landmarks:
        frame_idx += 1
        continue

    # Get landmark coordinates
    h, w, _ = frame.shape
    landmarks = pose_result.pose_landmarks.landmark

    # Use nose and shoulder points to define bounding box
    xs = np.array([lm.x * w for lm in landmarks])
    ys = np.array([lm.y * h for lm in landmarks])

    # Get the bounding box
    x_min = int(np.clip(np.min(xs) - 20, 0, w))
    x_max = int(np.clip(np.max(xs) + 20, 0, w))
    y_min = int(np.clip(np.min(ys) - 20, 0, h))
    y_max = int(np.clip(np.max(ys) + 20, 0, h))

    # Crop and save
    cropped = seg_image[y_min:y_max, x_min:x_max]

    # Skip empty crops
    if cropped.size == 0:
        frame_idx += 1
        continue

    cv2.imwrite(f"{output_folder}/frame_{frame_idx:04d}.jpg", cropped)
    frame_idx += 1

cap.release()
print(f"✅ Done. Cropped frames saved to: {output_folder}")


I0000 00:00:1750087121.231066 1167030 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1750087121.261270 1170380 gl_context.cc:357] GL version: 3.2 (OpenGL ES 3.2 NVIDIA 575.57.08), renderer: NVIDIA H100 80GB HBM3/PCIe/SSE2
I0000 00:00:1750087121.263907 1167030 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1750087121.291042 1170393 gl_context.cc:357] GL version: 3.2 (OpenGL ES 3.2 NVIDIA 575.57.08), renderer: NVIDIA H100 80GB HBM3/PCIe/SSE2


✅ Done. Cropped frames saved to: cropped_frames


In [4]:
from ultralytics import YOLO
import cv2
import os

# === Load YOLOv8-Pose model ===
model = YOLO("yolov8n-pose.pt")  # small & fast; use 'yolov8m-pose.pt' for better accuracy

# === Paths ===
input_path = "/home/siamai/data/week7/train/train/Gary Oldman/Gary Oldman Interview 2 (Descending).mp4"
output_folder = "cropped_left_person"
os.makedirs(output_folder, exist_ok=True)

# === Open video ===
cap = cv2.VideoCapture(input_path)
frame_idx = 0

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    # Run pose detection
    results = model(frame, conf=0.5)
    people = results[0].boxes.xyxy.cpu().numpy()  # person bounding boxes

    if len(people) == 0:
        frame_idx += 1
        continue

    # Select the leftmost person (smallest x_min)
    leftmost_idx = people[:, 0].argmin()
    x1, y1, x2, y2 = people[leftmost_idx]

    # Expand bounding box
    h, w, _ = frame.shape
    pad = 30  # pixels to expand
    x1 = max(int(x1 - pad), 0)
    y1 = max(int(y1 - pad), 0)
    x2 = min(int(x2 + pad), w)
    y2 = min(int(y2 + pad), h)

    # Crop without resizing
    cropped = frame[y1:y2, x1:x2]

    # Skip empty crop
    if cropped.size == 0:
        frame_idx += 1
        continue

    # Save cropped image
    out_path = os.path.join(output_folder, f"frame_{frame_idx:04d}.jpg")
    cv2.imwrite(out_path, cropped)

    frame_idx += 1

cap.release()
print(f"✅ Done. Cropped frames saved in: {output_folder}")

WARNING ⚠️ torchvision==0.20 is incompatible with torch==2.4.
Run 'pip install torchvision==0.19' to fix torchvision or 'pip install -U torch torchvision' to update both.
For a full compatibility table see https://github.com/pytorch/vision#installation


100%|██████████| 6.52M/6.52M [00:00<00:00, 33.8MB/s]



0: 384x640 2 persons, 46.7ms
Speed: 5.5ms preprocess, 46.7ms inference, 104.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 5.1ms
Speed: 3.5ms preprocess, 5.1ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.5ms
Speed: 1.1ms preprocess, 4.5ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.2ms
Speed: 0.9ms preprocess, 4.2ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 5.0ms
Speed: 0.9ms preprocess, 5.0ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 7.1ms
Speed: 1.0ms preprocess, 7.1ms inference, 1.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 5.9ms
Speed: 1.0ms preprocess, 5.9ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.3ms
Speed: 1.0ms preprocess, 4.3ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 6

In [ ]:
from ultralytics import YOLO
import cv2
import os

# === Load YOLOv8-Pose model ===
model = YOLO("yolov8n-pose.pt")  # You can also use 'yolov8m-pose.pt' for better accuracy

# === Paths ===
input_path = "/home/siamai/data/week7/train/train/Gary Oldman/Gary Oldman Interview 2 (Descending).mp4"
output_folder = "cropped_right_person"
os.makedirs(output_folder, exist_ok=True)

# === Open video ===
cap = cv2.VideoCapture(input_path)
frame_idx = 0

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    # Run pose detection
    results = model(frame, conf=0.5)
    people = results[0].boxes.xyxy.cpu().numpy()  # [x1, y1, x2, y2] for all detected people

    if len(people) == 0:
        frame_idx += 1
        continue

    # === ✅ Select the RIGHTMOST person (largest x1)
    rightmost_idx = people[:, 0].argmax()  # max of x1 (left edge of box)
    x1, y1, x2, y2 = people[rightmost_idx]

    # === Expand bounding box
    h, w, _ = frame.shape
    pad = 30  # how much to expand around the person
    x1 = max(int(x1 - pad), 0)
    y1 = max(int(y1 - pad), 0)
    x2 = min(int(x2 + pad), w)
    y2 = min(int(y2 + pad), h)

    # === Crop without resizing/stretching
    cropped = frame[y1:y2, x1:x2]

    # Skip if empty
    if cropped.size == 0:
        frame_idx += 1
        continue

    # === Save the cropped frame
    out_path = os.path.join(output_folder, f"frame_{frame_idx:04d}.jpg")
    cv2.imwrite(out_path, cropped)

    frame_idx += 1

cap.release()
print(f"✅ Done. Cropped frames saved in: {output_folder}")


0: 384x640 2 persons, 5.5ms
Speed: 1.4ms preprocess, 5.5ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.0ms
Speed: 0.9ms preprocess, 4.0ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 3.7ms
Speed: 0.9ms preprocess, 3.7ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 3.6ms
Speed: 0.8ms preprocess, 3.6ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 3.6ms
Speed: 0.8ms preprocess, 3.6ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 3.7ms
Speed: 0.7ms preprocess, 3.7ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 3.6ms
Speed: 0.8ms preprocess, 3.6ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 3.6ms
Speed: 0.8ms preprocess, 3.6ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)


In [8]:
from ultralytics import YOLO
from moviepy.editor import VideoFileClip
import numpy as np
import cv2

# Setup
model = YOLO("yolo11n-pose.pt")
input_path = "/home/siamai/data/week7/train/Gary Oldman/Gary Oldman Interview 2 (Descending).mp4"
output_path = "cropped_right_person.mp4"
pad = 30
conf_threshold = 0.3

# First pass: find a fixed crop size
clip = VideoFileClip(input_path)
fixed_size = None

def get_cropped_frame(frame):
    global fixed_size
    frame_bgr = cv2.cvtColor(frame, cv2.COLOR_RGB2BGR)
    h, w = frame_bgr.shape[:2]

    results = model(frame_bgr, conf=conf_threshold)
    boxes = results[0].boxes.xyxy.cpu().numpy()

    if len(boxes) == 0:
        return np.zeros_like(frame)  # black frame if no person

    rightmost_idx = boxes[:, 0].argmax()
    x1, y1, x2, y2 = boxes[rightmost_idx]

    x1 = max(int(x1 - pad), 0)
    y1 = max(int(y1 - pad), 0)
    x2 = min(int(x2 + pad), w)
    y2 = min(int(y2 + pad), h)

    if fixed_size is None:
        crop_w = x2 - x1
        crop_h = y2 - y1
        fixed_size = (crop_w, crop_h)

    crop = frame[y1:y1 + fixed_size[1], x1:x1 + fixed_size[0]]

    # Pad if necessary
    if crop.shape[0] != fixed_size[1] or crop.shape[1] != fixed_size[0]:
        crop = cv2.copyMakeBorder(
            crop,
            0, fixed_size[1] - crop.shape[0],
            0, fixed_size[0] - crop.shape[1],
            borderType=cv2.BORDER_CONSTANT,
            value=[0, 0, 0]
        )
    return crop

# Apply function to video
new_clip = clip.fl_image(get_cropped_frame)
new_clip.write_videofile(output_path, codec='libx264', fps=clip.fps)

print(f"✅ Saved cropped video to: {output_path}")


0: 384x640 2 persons, 5.2ms
Speed: 1.5ms preprocess, 5.2ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)
Moviepy - Building video cropped_right_person.mp4.
MoviePy - Writing audio in cropped_right_personTEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video cropped_right_person.mp4



t:   0%|          | 0/3576 [00:00<?, ?it/s, now=None]


0: 384x640 2 persons, 6.2ms
Speed: 1.5ms preprocess, 6.2ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.5ms
Speed: 0.8ms preprocess, 4.5ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.5ms
Speed: 0.9ms preprocess, 4.5ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.5ms
Speed: 0.8ms preprocess, 4.5ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.4ms
Speed: 0.8ms preprocess, 4.4ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.4ms
Speed: 0.8ms preprocess, 4.4ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.3ms
Speed: 0.7ms preprocess, 4.3ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.3ms
Speed: 0.8ms preprocess, 4.3ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)


t:   0%|          | 10/3576 [00:00<00:38, 93.52it/s, now=None]

...

t: 100%|█████████▉| 3559/3576 [00:41<00:00, 83.29it/s, now=None]


0: 384x640 2 persons, 4.1ms
Speed: 0.7ms preprocess, 4.1ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 5.6ms
Speed: 1.0ms preprocess, 5.6ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 5.2ms
Speed: 1.0ms preprocess, 5.2ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.9ms
Speed: 0.8ms preprocess, 4.9ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.9ms
Speed: 0.8ms preprocess, 4.9ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.8ms
Speed: 0.8ms preprocess, 4.8ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.8ms
Speed: 0.8ms preprocess, 4.8ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.8ms
Speed: 0.8ms preprocess, 4.8ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)


t: 100%|█████████▉| 3568/3576 [00:41<00:00, 82.67it/s, now=None]


0: 384x640 2 persons, 4.8ms
Speed: 0.8ms preprocess, 4.8ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.8ms
Speed: 0.8ms preprocess, 4.8ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.8ms
Speed: 0.8ms preprocess, 4.8ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.9ms
Speed: 0.8ms preprocess, 4.9ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.8ms
Speed: 0.8ms preprocess, 4.8ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.8ms
Speed: 0.8ms preprocess, 4.8ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.9ms
Speed: 0.8ms preprocess, 4.9ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 4.9ms
Speed: 0.8ms preprocess, 4.9ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)


Moviepy - Done !
Moviepy - video ready cropped_right_person.mp4
✅ Saved cropped video to: cropped_right_person.mp4


In [7]:
from moviepy.editor import VideoFileClip

clip = VideoFileClip("/home/siamai/data/week7/train/Gary Oldman/Gary Oldman Interview 2 (Descending).mp4")
print(f"Duration: {clip.duration}s, FPS: {clip.fps}, Total frames (approx): {int(clip.duration * clip.fps)}")

for i, frame in enumerate(clip.iter_frames()):
    print(f"Frame {i} shape: {frame.shape}")
    if i > 5:  # Just check first 6 frames
        break

Duration: 149.0s, FPS: 24.0, Total frames (approx): 3576
Frame 0 shape: (720, 1280, 3)
Frame 1 shape: (720, 1280, 3)
Frame 2 shape: (720, 1280, 3)
Frame 3 shape: (720, 1280, 3)
Frame 4 shape: (720, 1280, 3)
Frame 5 shape: (720, 1280, 3)
Frame 6 shape: (720, 1280, 3)


In [13]:
import cv2
import os
from glob import glob

image_folder = "cropped_right_person"
output_path = "joined_video.mp4"
fps = 24

image_paths = sorted(glob(os.path.join(image_folder, "*.jpg")))
print(f"🖼 Found {len(image_paths)} images")

if len(image_paths) == 0:
    raise ValueError("❌ No images found")

# Step 1: Find max width and height
max_w, max_h = 0, 0
for path in image_paths:
    img = cv2.imread(path)
    if img is not None:
        h, w = img.shape[:2]
        max_h = max(max_h, h)
        max_w = max(max_w, w)

print(f"📏 Target video size: {max_w}x{max_h}")

# Step 2: Create video writer
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
video_writer = cv2.VideoWriter(output_path, fourcc, fps, (max_w, max_h))

# Step 3: Pad each image
for img_path in image_paths:
    img = cv2.imread(img_path)
    if img is None:
        print(f"⚠️ Skipping unreadable file: {img_path}")
        continue

    h, w = img.shape[:2]

    top = (max_h - h) // 2
    bottom = max_h - h - top
    left = (max_w - w) // 2
    right = max_w - w - left

    padded_img = cv2.copyMakeBorder(
        img, top, bottom, left, right,
        borderType=cv2.BORDER_CONSTANT,
        value=(0, 0, 0)  # black padding
    )

    video_writer.write(padded_img)

video_writer.release()
print(f"✅ Saved padded video to: {output_path}")

🖼 Found 3575 images
📏 Target video size: 1078x710
✅ Saved padded video to: joined_video.mp4


In [ ]:
from ultralytics import YOLO
import cv2
import os
from glob import glob

# === INPUT VIDEO ===
input_path = "/home/siamai/data/week7/train/Benedict Cumberbatch Interview/Benedict Cumberbatch Interview.mp4"
video_name = os.path.splitext(os.path.basename(input_path))[0]  # "Gary Oldman Interview 2 (Descending)"
output_folder = f"{video_name}_cropped"
output_root = "output_videos"
os.makedirs(output_root, exist_ok=True)
output_video_path = os.path.join(output_root, f"{video_name}_cropped.mp4")
fps = 24  # You can read this from the video file if needed
# === Load YOLOv8-Pose model ===
model = YOLO("yolo11n-pose.pt")

# === Step 1: Extract cropped right-person frames ===
os.makedirs(output_folder, exist_ok=True)
cap = cv2.VideoCapture(input_path)
frame_idx = 0

while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    results = model(frame, conf=0.5)
    people = results[0].boxes.xyxy.cpu().numpy()

    if len(people) == 0:
        frame_idx += 1
        continue

    rightmost_idx = people[:, 0].argmax()  # max x1
    x1, y1, x2, y2 = people[rightmost_idx]

    h, w, _ = frame.shape
    pad = 30
    x1 = max(int(x1 - pad), 0)
    y1 = max(int(y1 - pad), 0)
    x2 = min(int(x2 + pad), w)
    y2 = min(int(y2 + pad), h)

    cropped = frame[y1:y2, x1:x2]
    if cropped.size == 0:
        frame_idx += 1
        continue

    out_path = os.path.join(output_folder, f"frame_{frame_idx:04d}.jpg")
    cv2.imwrite(out_path, cropped)
    frame_idx += 1

cap.release()
print(f"✅ Done. Cropped frames saved in: {output_folder}")

# === Step 2: Combine cropped frames into video ===
image_paths = sorted(glob(os.path.join(output_folder, "*.jpg")))
print(f"🖼 Found {len(image_paths)} cropped images")

if len(image_paths) == 0:
    raise ValueError("❌ No images found")

# Step 2.1: Determine max width and height
max_w, max_h = 0, 0
for path in image_paths:
    img = cv2.imread(path)
    if img is not None:
        h, w = img.shape[:2]
        max_h = max(max_h, h)
        max_w = max(max_w, w)

print(f"📏 Target video size: {max_w}x{max_h}")

# Step 2.2: Create video writer
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
video_writer = cv2.VideoWriter(output_video_path, fourcc, fps, (max_w, max_h))

# Step 2.3: Pad each image and write to video
for img_path in image_paths:
    img = cv2.imread(img_path)
    if img is None:
        print(f"⚠️ Skipping unreadable file: {img_path}")
        continue

    h, w = img.shape[:2]
    top = (max_h - h) // 2
    bottom = max_h - h - top
    left = (max_w - w) // 2
    right = max_w - w - left

    padded_img = cv2.copyMakeBorder(
        img, top, bottom, left, right,
        borderType=cv2.BORDER_CONSTANT,
        value=(0, 0, 0)  # black background
    )

    video_writer.write(padded_img)

video_writer.release()
print(f"🎬 Final video saved to: {output_video_path}")


0: 384x640 1 person, 4.5ms
Speed: 1.0ms preprocess, 4.5ms inference, 0.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 4.1ms
Speed: 1.0ms preprocess, 4.1ms inference, 0.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 4.3ms
Speed: 0.9ms preprocess, 4.3ms inference, 0.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 4.3ms
Speed: 0.8ms preprocess, 4.3ms inference, 0.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 4.1ms
Speed: 0.8ms preprocess, 4.1ms inference, 0.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 4.1ms
Speed: 0.7ms preprocess, 4.1ms inference, 0.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 4.1ms
Speed: 0.7ms preprocess, 4.1ms inference, 0.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 4.1ms
Speed: 0.7ms preprocess, 4.1ms inference, 0.4ms postprocess pe

In [ ]:
from ultralytics import YOLO
import cv2
import os

# === Input/Output Settings ===
input_path = "/home/siamai/data/week7/train/s02_smiley.mp4"
video_name = os.path.splitext(os.path.basename(input_path))[0]
output_root = "output_videos"
os.makedirs(output_root, exist_ok=True)
output_video_path = os.path.join(output_root, f"{video_name}_cropped.mp4")
batch_size = 16
pad = 30

# === Load model ===
model = YOLO("yolo11n-pose.pt")
model.to('cuda')

# === Open video ===
cap = cv2.VideoCapture(input_path)
fps = cap.get(cv2.CAP_PROP_FPS) or 24

# === Read and batch frames ===
frames = []
cropped_frames = []
max_w, max_h = 0, 0

def process_batch(batch):
    global max_w, max_h
    results = model(batch, conf=0.5)
    for frame, result in zip(batch, results):
        boxes = result.boxes.xyxy.cpu().numpy()
        if len(boxes) == 0:
            continue

        rightmost_idx = boxes[:, 0].argmax()
        x1, y1, x2, y2 = boxes[rightmost_idx]
        h, w, _ = frame.shape

        x1 = max(int(x1 - pad), 0)
        y1 = max(int(y1 - pad), 0)
        x2 = min(int(x2 + pad), w)
        y2 = min(int(y2 + pad), h)

        cropped = frame[y1:y2, x1:x2]
        if cropped.size == 0:
            continue

        ch, cw = cropped.shape[:2]
        max_h = max(max_h, ch)
        max_w = max(max_w, cw)
        cropped_frames.append(cropped)

# === Read and batch frames ===
while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break
    frames.append(frame)
    if len(frames) == batch_size:
        process_batch(frames)
        frames = []

# Process leftover frames
if frames:
    process_batch(frames)
cap.release()

print(f"✅ Cropped {len(cropped_frames)} frames")

# === Write video ===
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
video_writer = cv2.VideoWriter(output_video_path, fourcc, fps, (max_w, max_h))

for cropped in cropped_frames:
    h, w = cropped.shape[:2]
    top = (max_h - h) // 2
    bottom = max_h - h - top
    left = (max_w - w) // 2
    right = max_w - w - left

    padded = cv2.copyMakeBorder(cropped, top, bottom, left, right,
                                 borderType=cv2.BORDER_CONSTANT, value=(0, 0, 0))
    video_writer.write(padded)

video_writer.release()
print(f"🎬 Final video saved to: {output_video_path}")


WARNING ⚠️ torchvision==0.20 is incompatible with torch==2.4.
Run 'pip install torchvision==0.19' to fix torchvision or 'pip install -U torch torchvision' to update both.
For a full compatibility table see https://github.com/pytorch/vision#installation

0: 384x640 (no detections), 4.5ms
1: 384x640 (no detections), 4.5ms
2: 384x640 (no detections), 4.5ms
3: 384x640 (no detections), 4.5ms
4: 384x640 (no detections), 4.5ms
5: 384x640 (no detections), 4.5ms
6: 384x640 (no detections), 4.5ms
7: 384x640 (no detections), 4.5ms
8: 384x640 (no detections), 4.5ms
9: 384x640 (no detections), 4.5ms
10: 384x640 (no detections), 4.5ms
11: 384x640 (no detections), 4.5ms
12: 384x640 (no detections), 4.5ms
13: 384x640 (no detections), 4.5ms
14: 384x640 (no detections), 4.5ms
15: 384x640 (no detections), 4.5ms
Speed: 1.2ms preprocess, 4.5ms inference, 1.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 (no detections), 0.3ms
1: 384x640 (no detections), 0.3ms
2: 384x640 (no detections), 0.3

In [ ]:
from ultralytics import YOLO
import cv2
import os

# === Input/output setup ===
input_path = "/home/siamai/data/week7/train/Benedict Cumberbatch Interview/Benedict Cumberbatch Interview.mp4"
video_name = os.path.splitext(os.path.basename(input_path))[0]
output_root = "output_videos"
os.makedirs(output_root, exist_ok=True)
output_video_path = os.path.join(output_root, f"{video_name}_cropped.mp4")

# === Load model to GPU ===
model = YOLO("yolo11n-pose.pt").to('cuda')

# === Open video ===
cap = cv2.VideoCapture(input_path)
fps = cap.get(cv2.CAP_PROP_FPS) or 24
width = int(cap.get(cv2.CAP_PROP_FRAME_WIDTH))
height = int(cap.get(cv2.CAP_PROP_FRAME_HEIGHT))

# === Setup video writer ===
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
video_writer = cv2.VideoWriter(output_video_path, fourcc, fps, (width, height))

# === Frame processing loop ===
pad = 30
while cap.isOpened():
    ret, frame = cap.read()
    if not ret:
        break

    results = model(frame, conf=0.5)
    people = results[0].boxes.xyxy.cpu().numpy()

    if len(people) > 0:
        # Select rightmost person (max x1)
        rightmost_idx = people[:, 0].argmax()
        x1, y1, x2, y2 = people[rightmost_idx]

        # Expand box with padding
        x1 = max(int(x1 - pad), 0)
        y1 = max(int(y1 - pad), 0)
        x2 = min(int(x2 + pad), width)
        y2 = min(int(y2 + pad), height)

        cropped = frame[y1:y2, x1:x2]
        # Pad to match original frame size
        ch, cw = cropped.shape[:2]
        top = (height - ch) // 2
        bottom = height - ch - top
        left = (width - cw) // 2
        right = width - cw - left

        padded = cv2.copyMakeBorder(
            cropped, top, bottom, left, right,
            borderType=cv2.BORDER_CONSTANT,
            value=(0, 0, 0)
        )
        video_writer.write(padded)
    else:
        # No detection — keep original frame
        video_writer.write(frame)

cap.release()
video_writer.release()
print(f"✅ Final video saved to: {output_video_path}")